# Euler Problem 14

The following iterative sequence is defined for the set of positive integers:

n → n/2 (n is even)
n → 3n + 1 (n is odd)

Using the rule above and starting with 13, we generate the following sequence:

$13 → 40 → 20 → 10 → 5 → 16 → 8 → 4 → 2 → 1$

It can be seen that this sequence (starting at 13 and finishing at 1) contains 10 terms. Although it has not been proved yet (Collatz Problem), it is thought that all starting numbers finish at 1.

Which starting number, under one million, produces the longest chain?

NOTE: Once the chain starts the terms are allowed to go above one million.

I would go for a recursive function with a cache here. This should give us good performance with acceptable memory footprint.

In [1]:
from functools import lru_cache
from collections import deque

@lru_cache(maxsize=11000000)
def get_collatz_sequence(n):
    if n == 1:
        return deque([1])
    ds = get_collatz_sequence(n // 2) if n % 2 == 0 else get_collatz_sequence(3 * n + 1)
    ds.appendleft(n)
    return ds

assert(list(get_collatz_sequence(13)) == [13, 40, 20, 10, 5, 16, 8, 4, 2, 1])

Isn't this a beautiful solution? We need a deque to appendleft. Of course, we could also use a regular list and reverse the result, but it is nicer to get the correct solution out right away. Now we simply force the solution.

In [2]:
try:
    s = max([(len(get_collatz_sequence(i)), i) for i in range(1000000)])
    print(s)
    assert(s == 837799)
except RecursionError:
    print("Okay, we need a loop.")


Okay, we need a loop.


In [3]:
cache = {}

def get_collatz_sequence(n):
    global cache
    orig_n = n
    cs = []
    while n != 1:
        if n in cache:
            cs = cs + cache[n]
            cache[orig_n] = cs
            return cs
        cs.append(n)
        n = n // 2 if n % 2 == 0 else 3 * n + 1
    cs.append(n)
    for i in range(len(cs)):
        cache[cs[i]] = cs[i:]
    return cs

assert(list(get_collatz_sequence(13)) == [13, 40, 20, 10, 5, 16, 8, 4, 2, 1])

def brute_force():
    return max([(len(get_collatz_sequence(i)), i) for i in range(1, 1000000)])[1]

s = brute_force()
assert(s == 837799)

import timeit
print(timeit.timeit(brute_force, number=10))
print(brute_force())

11.4885111964837
837799


Here we go. Takes some time. We could optimize by caching only the length and not the complete list.